In [1]:
# %pip install gputil
# %pip install setuptools
# %pip install transformers
# %pip install torch

# %pip install auto-gptq #==0.4.0

This notebook attempts to open up 2 LMM models, and swap out the input and output embeddings and tokenizer.
It then runs the model to see if the output still makes sense (hint: actually I dont think you need a hint)

Be mindful of the difference between weights[:]= and weights= (I may have messed that up at times)

In [2]:
import GPUtil

from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline
import torch
# from auto_gptq import AutoGPTQForCausalLM

/home/mick/pycharmprojects/Frankenstein/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/mick/pycharmprojects/Frankenstein/.venv/lib/python3.12/site-packages/transformers/loss/loss_for_object_detection.py:28: UserWarning: A NumPy version >=1.22.4 and <2.3.0 is required for this version of SciPy (detected version 2.3.0)
  from scipy.optimize import linear_sum_assignment


In [3]:
gpus = GPUtil.getGPUs()
if not gpus:
    print("No GPU detected on this system.")
else:
    for gpu in gpus:
        print(f"GPU Name: {gpu.name}")
        print(f"Total VRAM: {gpu.memoryTotal} MB")
        print(f"Free VRAM: {gpu.memoryFree} MB")
        print(f"Used VRAM: {gpu.memoryUsed} MB")
        print("-" * 40)

No GPU detected on this system.


In [4]:
def grab_model(model_name, quantized = False):
    if quantized:
        model = AutoGPTQForCausalLM.from_quantized(model_name, device="cpu", use_safetensors=True)
    else:
        model = AutoModelForCausalLM.from_pretrained(model_name)

    tokenizer = AutoTokenizer.from_pretrained(model_name)
    return model, tokenizer

In [5]:
# Download 2 models.

modelA, tokenizerA = grab_model("gpt2")
modelB, tokenizerB = grab_model("EleutherAI/gpt-neo-125M")

# modelA, tokenizerA = grab_model("EleutherAI/gpt-neo-125M-4bit", quantized=True)
# modelB, tokenizerB = grab_model("iproskurina/opt-125m-GPTQ-4bit-g128", quantized=True)

In [6]:
# Check if the dimensionality is identical
modelA.config.hidden_size == modelB.config.hidden_size 

True

In [7]:
## ATTEMPT 1: 
## replace input and output embeddings (tied), 
## optionally resize token embeddings (probably not needed, definitely not needed if tokenizer is the same)
## optionally also swap the positional encoding (wpe) 


### replace tokenizer:
## modelA.Tokenizer = tokenizerB   # not necessary: the pipeline will not access this directly anyway

## replace token embeddings for input and output:
# modelA.set_input_embeddings(modelB.get_input_embeddings())
# modelA.lm_head.weight = modelB.get_input_embeddings().weight
# modelA.resize_token_embeddings(tokenizerB.vocab_size)

# modelA.transformer.wpe.weight = modelB.transformer.wpe.weight



In [8]:
## ATTEMPT 2:
## add a scaling factor, attempting to normalize weight magnitude to match the other model better

# emb1 = modelA.get_input_embeddings().weight
# emb2 = modelB.get_input_embeddings().weight

# print("ModelA mean norms:", torch.norm(emb1, dim=1).mean().item())
# print("ModelB mean norms:", torch.norm(emb2, dim=1).mean().item())

# scaling_factor = torch.norm(emb1, dim=1).mean().item() / torch.norm(emb2, dim=1).mean().item()

# print(scaling_factor)

# new_embedding = torch.nn.Embedding.from_pretrained(emb2*scaling_factor)

# print("new_embedding mean norms:", torch.norm(new_embedding.weight, dim=1).mean().item())

# modelA.set_input_embeddings(new_embedding)
# modelA.lm_head.weight = new_embedding.weight


In [9]:
# check the max and mean values (should not be too big) and nan values (should not occur)

print(torch.isnan(modelB.get_input_embeddings().weight).any())
print(torch.norm(modelB.get_input_embeddings().weight, dim=1).max())
print(torch.norm(modelB.get_input_embeddings().weight, dim=1).mean())

tensor(False)
tensor(22.2842, grad_fn=<MaxBackward1>)
tensor(11.5013, grad_fn=<MeanBackward0>)


In [10]:
# optional check if the resulting rotational matrix is an orthogonal rotation matrix (it should be, within e-5 ish)
def check_orthogonal(R):
    I = torch.eye(R.size(0), device=R.device)
    delta = torch.norm(R.T @ R - I)
    print(f"Delta: {delta:.6e}")
    

In [11]:
# use proscrustes:
def procrustes(A: torch.Tensor, B: torch.Tensor) -> torch.Tensor:
    # center the model - recommended not to do this.. 
    # rotational matrix may improve but the shift kills everything
    # if you do this, probably should shift it back afterwards again in the rotated frame.
    # A_centered = A - A.mean(dim=0, keepdim=True)
    # B_centered = B - B.mean(dim=0, keepdim=True)

    #M = B_centered.T @ A_centered
    M = B.T @ A

    # find optimal rotation with svd
    U, _, Vt = torch.linalg.svd(M)

    # get rotation matrix that aligns B to A
    R = U @ Vt

    check_orthogonal(R)
    
    return B @ R # return rotated tensor B

def get_rotated_matrix(A, B, n = 1000):
    # use only the first n tokens for rotation:
    # return procrustes(A[:n], B[:n])
    # or use all, if the model is small enough (it's usually fine, and a badly rotated matrix causes problems):
    return procrustes(A, B)
    




In [12]:
# THIRD ATTEMPT:
# try aligning with Procrustes first before swapping. Still also uses rescaling.

emb1 = modelA.get_input_embeddings().weight
emb2 = modelB.get_input_embeddings().weight

emb2_R = get_rotated_matrix(emb1, emb2)

print("ModelA mean norms:", torch.norm(emb1, dim=1).mean().item())
print("ModelB mean norms:", torch.norm(emb2, dim=1).mean().item())
print("Rotated modelB mean norms:", torch.norm(emb2_R, dim=1).mean().item())

scaling_factor = torch.norm(emb1, dim=1).mean().item() / torch.norm(emb2_R, dim=1).mean().item()

print(scaling_factor)

new_embedding = torch.nn.Embedding.from_pretrained(emb2_R*scaling_factor)
# new_embedding = torch.nn.Embedding.from_pretrained(emb2_R)


print("new_embedding mean norms:", torch.norm(new_embedding.weight, dim=1).mean().item())

modelA.set_input_embeddings(new_embedding)
modelA.lm_head.weight = new_embedding.weight


Delta: 6.659338e-05
ModelA mean norms: 3.9585366249084473
ModelB mean norms: 11.50130844116211
Rotated modelB mean norms: 11.501314163208008
0.3441812447460622
new_embedding mean norms: 3.958536148071289


In [13]:
# optionally swap the position encoding weights.
modelA.transformer.wpe.weight = modelB.transformer.wpe.weight

In [14]:
# check if the output shape matches the tokenizer vocab size (it should)
modelA.lm_head.out_features == tokenizerA.vocab_size

True

In [15]:
# code to make extra sure the input and output weights are tied (if you don't trust that they are in your model)
# usually this should change nothing: they are often even the same object if they are tied.
# plus we already set this explicitly before, even if it was probably not needed:

# modelA.lm_head.weight = modelA.get_input_embeddings().weight 


In [21]:
# use model
pipe = pipeline("text-generation", model=modelA, tokenizer=tokenizerB)
print(pipe("Hello, how are you?"))

Device set to use cpu
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


[{'generated_text': 'Hello, how are you? he he he he he he sir he he he he he he he he he he he he he he I I he he he he he he he he he he he he he he he he he sir he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he but he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he he I he he he he he he he he he he he he he he he he he he he he he he he he he but he sir he he he he he he he he he he he he but he he he he he he he he he he he he he I he he but he he he he he he he he he he he he he he he he he I he he he he he I he he he he he he he he he he he he he he he he he he he he he he he he he he I he he he he he he he he he he'}]


In [17]:
# extra check that input and output weights match
modelA.lm_head.weight.data_ptr() == modelA.get_input_embeddings().weight.data_ptr()

True

In [18]:
# extra check that input and output weights match
modelB.lm_head.weight.data_ptr() == modelB.get_input_embeddings().weight.data_ptr()

True

In [19]:
# print the token IDs for the given string -> turns out these gpt2 and neo use the same tokenizer
# thats why swapping them in the pipeline had no effect at all (by itself should break model unless identical) 
tok = tokenizerA("This is a test and i wonder why the tokenizers are the same", return_tensors = "pt")
print(tok.input_ids[0])

tensor([ 1212,   318,   257,  1332,   290,  1312,  4240,  1521,   262, 11241,
        11341,   389,   262,   976])


In [20]:
tok = tokenizerB("This is a test and i wonder why the tokenizers are the same", return_tensors = "pt")
print(tok.input_ids[0])

tensor([ 1212,   318,   257,  1332,   290,  1312,  4240,  1521,   262, 11241,
        11341,   389,   262,   976])
